In [1]:
import holoviews as hv
import panel as pn
import pandas as pd

pn.extension('vizzu', 'tabulator', design='material', template='material')
import hvplot.pandas

## Load data

In [2]:
windturbines = pn.state.as_cached(
    'windturbines',
    pd.read_parquet,
    path='https://datasets.holoviz.org/windturbines/v1/windturbines.parq'
)

windturbines.head()

case_id    faa_ors           faa_asn  usgs_pr_id   eia_id t_state  \
0  3072661       None              None      5149.0  52161.0      CA   
1  3072695       None              None      5143.0  52161.0      CA   
2  3072704       None              None      5146.0  52161.0      CA   
3  3063272  19-028134  2014-WTE-4084-OE         NaN      NaN      IA   
4  3053390  19-028015  2015-WTE-6386-OE         NaN      NaN      IA   

       t_county  t_fips                   p_name  p_year  ...  retrofit  \
0   Kern County    6029                 251 Wind  1987.0  ...         0   
1   Kern County    6029                 251 Wind  1987.0  ...         0   
2   Kern County    6029                 251 Wind  1987.0  ...         0   
3  Story County   19169  30 MW Iowa DG Portfolio  2017.0  ...         0   
4  Boone County   19015  30 MW Iowa DG Portfolio  2017.0  ...         0   

   retrofit_year t_conf_atr t_conf_loc  t_img_date     t_img_srce       xlong  \
0            NaN          2          3  2018-05-08  Digital Globe -118.363762   
1            NaN          2          3  2018-05-08  Digital Globe -118.364410   
2            NaN          2          3  2018-05-08  Digital Globe -118.364197   
3            NaN          3          3  2017-04-24  Digital Globe  -93.430367   
4            NaN          3          3  2017-06-01  Digital Globe  -93.700424   

        ylat       easting      northing  
0  35.077908 -1.317619e+07  4.174474e+06  
1  35.077435 -1.317627e+07  4.174409e+06  
2  35.077644 -1.317624e+07  4.174438e+06  
3  42.028233 -1.040062e+07  5.165210e+06  
4  41.977608 -1.043068e+07  5.157626e+06  

[5 rows x 29 columns]

## Plot data

In [3]:
def data(df, groupby, quant):
    if quant == 'Count':
        return df.value_counts(groupby).to_frame(name='Count').sort_index().reset_index().iloc[:50]
    else:
        return df.groupby(groupby)[quant].sum().reset_index().iloc[:50]

def config(chart_type, groupby, quant):
    if chart_type == 'Bubble Chart':
        return {
            "channels": {
                "x": None,
                "y": None,
                "color": groupby,
                "label": groupby,
                "size": quant
            },
            'geometry': 'circle'
        }
    else:
        return {
            "channels": {
                "x": groupby,
                "y": quant,
                "color": None,
                "label": None,
                "size": None
            },
            'geometry': 'rectangle'
        }
    
ls = hv.link_selections.instance()

geo = ls(windturbines.hvplot.points(
    'easting', 'northing', xaxis=None, yaxis=None, rasterize=True, xlim=(-15000000, -5000000),
    tiles='CartoLight', height=500, responsive=True, dynspread=True, cnorm='log', cmap='plasma'
))
    
groupby = pn.widgets.RadioButtonGroup(options={'State': 't_state', 'Year': 'p_year', 'Manufacturer': 't_manu'}, align='center')
chart_type = pn.widgets.RadioButtonGroup(options=['Bar Chart', 'Bubble Chart'], align='center')
quant = pn.widgets.RadioButtonGroup(options={'Count': 'Count', 'Capacity': 'p_cap'}, align='center')
lsdata = ls.selection_param(windturbines)

vizzu = pn.pane.Vizzu(
    pn.bind(data, lsdata, groupby, quant),
    config=pn.bind(config, chart_type, groupby, quant),
    column_types={'p_year': 'dimension'},
    style={
        "plot": {
            "xAxis": {
                "label": {
                    "angle": "-45deg"
                }
            }
        }
    },
    sizing_mode='stretch_both'
)

def format_df(df):
    df = df[['t_state', 't_county', 'p_name', 'p_year', 't_manu', 't_cap']]
    return df.rename(
        columns={col: col.split('_')[1].title() for col in df.columns}
    )


table = pn.widgets.Tabulator(
    pn.bind(format_df, lsdata), page_size=8, pagination='remote',
    show_index=False,
)

pn.Column(
    pn.Row(quant, "# by", groupby, "# as a", chart_type).servable(area='header'),
    pn.Column(
        pn.Row(geo, table),
        vizzu, min_height=1000,
        sizing_mode='stretch_both'
    ).servable(title='Windturbines')
)

Column(design=<class 'panel.theme.materi...)
    [0] Row(design=<class 'panel.theme.materi...)
        [0] RadioButtonGroup(align='center', design=<class 'panel.theme.materi..., options={'Count': 'Count', ...}, value='Count')
        [1] Markdown(str, design=<class 'panel.theme.materi...)
        [2] RadioButtonGroup(align='center', design=<class 'panel.theme.materi..., options={'State': 't_state', ...}, value='t_state')
        [3] Markdown(str, design=<class 'panel.theme.materi...)
        [4] RadioButtonGroup(align='center', design=<class 'panel.theme.materi..., options=['Bar Chart', ...], value='Bar Chart')
    [1] Column(design=<class 'panel.theme.materi..., min_height=1000, sizing_mode='stretch_both')
        [0] Row(design=<class 'panel.theme.materi...)
            [0] HoloViews(DynamicMap, design=<class 'panel.theme.materi..., height=500, sizing_mode='stretch_width')
            [1] Tabulator(design=<class 'panel.theme.materi..., page_size=8, pagination='remote', show_index=False, value=      State   ...)
        [1] Vizzu(DataFrame, column_types={'p_year': 'dimension'}, config={'channels': {'x': 't_stat...}, design=<class 'panel.theme.materi..., sizing_mode='stretch_both', style={'plot': {'xAxis': {...})